# Find the GW skies which would have been detected

In [1]:
#!/usr/bin/env python
"""step2_find_detected_GW_skies.ipynb: a notebook to find detectable GW skies """

__author__ = "Chiara M. F. Mingarelli"
__copyright__ = "Copyright 2016, GWASAP project"
__credits__ = ["Chiara Mingarelli"]
__license__ = "GPL"
__version__ = "0.0.1"
__maintainer__ = "Chiara Mingarelli"
__email__ = "mingarelli@gmail.com"

In [ ]:
"""
In step 2:

    - gather all the data from the realizations
    - analyze the red shift of random galaxies
    - analyza the number of sources per realization
    - analyze the number of stalled binaries per realization
    - compiles a file with all the skies that have a potemtial detectable source
"""

In [2]:
from __future__ import division
import os
from IPython.display import display, Math, Latex
import math
from math import sqrt, cos, sin, pi
import numpy as np
import statsmodels.api as sm
from scipy.interpolate import interp1d
import scipy.integrate
import matplotlib.pyplot as plt
import matplotlib.mlab as ml
from matplotlib.ticker import FormatStrFormatter, LinearLocator, NullFormatter, NullLocator, MultipleLocator
import matplotlib.ticker
import matplotlib.colors
from matplotlib.font_manager import FontProperties
from matplotlib import rc, text
import healpy as hp
#import plot_mpI2
from astropy import units as u
from astropy.coordinates import SkyCoord
from astropy.io import fits
from scipy.stats import norm
import matplotlib.mlab as mlab
from scipy import stats


%matplotlib inline
%config InlineBackend.figure_format = "retina"

In [3]:
nside = 2**6

#available GW frequencies
freq_choice = np.loadtxt("../gw_freqs1.dat") 

In [4]:
data_filename = "../../fake_data/MM13_big_test.txt"

In [5]:
# Retreives the data from the data file and seperates the data into its corresponding
# array and further seperates by realization


count = 0 #variable used to count number of sources per realization
file_s = [] #numbers of sources per relaization
RA = []
DEC = []
freq = []
strain = []
mchirp_rec = []
q_rec = []
gal_cat = [] #string
dist = []
mstar = []
save_p = []
gal_choice = []
T_z = []
mergeRate = []
t2c = []
z = []
stall = []  
stall_num = 0

#temps used to help seperate data by relalization
temp_RA = []
temp_DEC = []
temp_freq = []
temp_strain = []
temp_mchirp_rec = []
temp_q_rec = []
temp_gal_cat = [] #string
temp_dist = []
temp_mstar = []
temp_save_p = []
temp_gal_cat = []
temp_gal_choice = []
temp_T_z = []
temp_mergRate = []
temp_t2c = []
temp_z = []
temp_file_s = []

with open(data_filename) as f:
    
    temp_RA = []
    temp_DEC = []
    temp_freq = []
    temp_strain = []
    temp_mchirp_rec = []
    temp_q_rec = []
    temp_gal_cat = [] #string
    temp_dist = []
    temp_mstar = []
    temp_save_p = []
    temp_gal_choice = []
    temp_T_z = []
    temp_mergRate = []
    temp_t2c = []
    temp_z = []
    temp_file_s = []
    
    for line in f:
        if len(line) < 50:
            
            #add the collected data to the real lists
            
            file_s.append(count)
            stall.append(stall_num)
            RA.append(temp_RA) #phi, add pi to this for healpix maps
            DEC.append(temp_DEC) #theta
            freq.append(temp_freq)
            strain.append(temp_strain)
            mchirp_rec.append(temp_mchirp_rec)
            q_rec.append(temp_q_rec)
            gal_cat.append(temp_gal_cat)
            dist.append(temp_dist)
            mstar.append(temp_mstar)
            save_p.append(temp_save_p)
            gal_choice.append(temp_gal_choice)
            T_zt.append(temp_T_z)
            mergeRate.append(temp_mergRate) 
            t2c.append(temp_t2c)
            z.append(temp_z)
            
            #reset the temp lists
            
            temp_RA = []
            temp_DEC = []
            temp_freq = []
            temp_strain = []
            temp_mchirp_rec = []
            temp_q_rec = []
            temp_gal_cat = [] #string
            temp_distt = []
            temp_mstar = []
            temp_save_p = []
            temp_gal_cat = []
            temp_gal_choice = []
            temp_T_z = []
            temp_mergRate = []
            temp_t2c = []
            temp_z = []
            temp_file_s = []
            count = 0
            
        else:
            
            #data is split into its corresponding lists
            
            splitted = line.split(" ") 
    
            stall_num = int(splitted[-1])
            temp_RA.append(float(splitted[0])) #phi, add pi to this for healpix maps
            temp_DEC.append(float(splitted[1])) #theta
            temp_freq.append(float(splitted[2]))
            temp_strain.append(float(splitted[3]))
            temp_mchirp_rec.append(float(splitted[4]))
            temp_q_rec.append(float(splitted[5]))
            temp_gal_cat.append(str(splitted[6]))
            temp_dist.append(float(splitted[7]))
            temp_mstar.append(float(splitted[8]))
            temp_save_p.append(float(splitted[9]))
            temp_gal_choice.append(float(splitted[10]))
            temp_T_z.append(float(splitted[11]))
            temp_mergRate.append(float(splitted[12])) 
            temp_t2c.append(float(splitted[13]))
            temp_z.append(float(splitted[14]))
            count+=1
            
            
#adding final realization
file_s.append(count)
stall.append(stall_num)
RA.append(temp_RA) #phi, add pi to this for healpix maps
DEC.append(temp_DEC) #theta
freq.append(temp_freq)
strain.append(temp_strain)
mchirp_rec.append(temp_mchirp_rec)
q_rec.append(temp_q_rec)
gal_cat.append(temp_gal_cat)
dist.append(temp_dist)
mstar.append(temp_mstar)
save_p.append(temp_save_p)
gal_choice.append(temp_gal_choice)
T_z.append(temp_T_z)
mergeRate.append(temp_mergRate) 
t2c.append(temp_t2c)
z.append(temp_z)


#deleting intial empty array ex) stall = [[], [2], [3]] --> [[2], [3]]
file_s = file_s[1:]
stall = stall[1:]
RA = RA[1:]
DEC = DEC[1:]
freq = freq[1:]
strain = strain[1:]
mchirp_rec = mchirp_rec[1:]
q_rec = q_rec[1:]
gal_cat = gal_cat[1:]
dist = dist[1:]
mstar[1:]
save_p[1:]
gal_choice[1:]
T_z[1:]
mergeRate = mergeRate[1:]
t2c = t2c[1:]
z = z[1:]
    
    


In [7]:
def find_nearest(array ,value):
    idx = (np.abs(array-value)).argmin()
    return array[idx]

In [ ]:
#Paramters for so all plots look similar

fig_width_pt = 245.27 #513.17           # Get this from LaTeX using \showthe\columnwidth
inches_per_pt = 1.0/72.27               # Convert pt to inches
golden_mean = (np.sqrt(5)-1.0)/2.0      # Aesthetic ratio
fig_width = fig_width_pt*inches_per_pt  # width in inches
fig_height =fig_width*golden_mean       # height in inches
fig_size = [fig_width,fig_height]

params = {'backend': 'pdf',
        'axes.labelsize': 7,
        'lines.markersize': 4,
        'font.size': 7,
        'xtick.major.size':6,
        'xtick.minor.size':3,  
        'ytick.major.size':6,
        'ytick.minor.size':3, 
        'xtick.major.width':0.5,
        'ytick.major.width':0.5,
        'xtick.minor.width':0.5,
        'ytick.minor.width':0.5,
        'lines.markeredgewidth':1,
        'axes.linewidth':1.2,
        'legend.fontsize': 7,
        'xtick.labelsize': 7,
        'ytick.labelsize': 7,
        'savefig.dpi':200,
        'path.simplify':True,
        'font.family': 'serif',
        #'font.serif':'Times',
        'text.latex.preamble': [r'\usepackage{amsmath}'],
        'text.usetex':True,
        #'axes.color_cycle': ['b', 'lime', 'r', 'purple', 'g', 'c', 'm', 'orange', 'darkblue', \
        #                        'darkcyan', 'y','orangered','chartreuse','brown','deeppink','lightgreen', 'k'],
        #'font.serif':cm,
        'figure.figsize': fig_size}
plt.rcParams.update(params)

In [ ]:
#methods to normalize histograms

def hist_weight(lst):
    return np.ones_like(lst)/len(lst)

def auto_bin(bin_size, min_edge, max_edge):
    # for nice looking bins
    N = (max_edge-min_edge)/bin_size; Nplus1 = N + 1
    bin_list = np.linspace(min_edge, max_edge, Nplus1)
    return bin_list

In [ ]:
#choose number galxies to analyze their redshift

num_galaxies = 10 #change to whatever you want to test with (note: doing more than 50 takes a long time)
ran_z = np.random.choice(z, num_galaxies, replace=False)

In [ ]:
#plots the redshift (z) of the selected galaxies 

hist_bin = auto_bin(.2, .1, 4)

test = []

for i in range(len(ran_z)):
    test.append(plt.hist(ran_z[i], hist_bin, weights = hist_weight(ran_z[i])))
    
plt.ylabel("Count")
plt.xlabel("redshift $z$ of galaxy-galaxy merger")  
plt.tight_layout()


#plt.savefig("plots_sigma_114/step_2/114_redshift_mm13.pdf")

In [ ]:
#gathers the mean and variance of the galaxies in each bin (takes a while)

no_of_bins = hist_bin.size #20
avg_test = []
tMean = []
tStd = []

for j in range(no_of_bins - 1):
    
    for i in range(len(ran_z)):
        #inst = values of histpgram, bins, pathes
        inst = plt.hist(z_list[i], hist_bin, weights = hist_weight(z_list[i]))[0][j]
        avg_test.append(inst)
        
    tMean.append(np.mean(avg_test))
    tStd.append(np.std(avg_test))
    avg_test = []
    
    print ("Mean value for j is ", tMean[j], j) 

In [ ]:
#causes error otherwise
hist_bin = hist_bin[:-1]
print(hist_bin)

In [ ]:
#plot the average redshift with error for each bin

fig, ax = plt.subplots()
ax.bar(hist_bin, tMean, yerr=tStd,edgecolor = 'black', width = 0.2, alpha = 0.8)

plt.xlim(0,4)
plt.ylim(0,.4)

majorLocator = MultipleLocator(.3)
ax.xaxis.set_major_locator(majorLocator)

plt.ylabel("Probability")
plt.xlabel("Redshift $z$ of galaxy-galaxy merger")
plt.tight_layout()

#plt.savefig("plots_sigma_114/step_2/114_redshift_avg_mm13_sig.pdf")

In [ ]:
#plot the number of stalled sources per reliazation

weightsSt =  np.ones_like(stall)/len(stall) #need for normalization

bin_size = 1; min_edge = min(stall); max_edge = max(stall)
N = (max_edge-min_edge)/bin_size; Nplus1 = N + 1
bin_list = np.linspace(min_edge, max_edge, Nplus1)

(mu, sigma) = norm.fit(stall) #mean and variance

print(mu, sigma)

shape, loc, scale = scipy.stats.lognorm.fit(stall)

y = mlab.normpdf(bin_list, mu, sigma)
l = plt.plot(bin_list, y, 'r--', linewidth=2)
plt.hist(stall, bin_list, weights = weightsSt, alpha =0.8, align='left')

plt.ylabel("Probability")
plt.xlabel("Number of Stalled Binaries per realization")
plt.tight_layout()

#plt.savefig("plots_sigma_114/step_2/114_no_stalled_mm13.pdf")


In [ ]:
#plot the number of sources per relaization

weightsG = np.ones_like(file_s)/len(file_s)
bin_size = 1; min_edge = min(file_s) ; max_edge = max(file_s)
N = (max_edge-min_edge)/bin_size; Nplus1 = N + 1
bin_list = np.linspace(min_edge, max_edge, Nplus1)

(mu, sigma) = norm.fit(file_s) #mean and variance
print(mu, sigma)



y = mlab.normpdf(bin_list, mu, sigma)
l = plt.plot(bin_list, y, 'r--', linewidth=2)
plt.hist(file_s, bin_list, weights = weightsG, alpha =0.8, align='left')

plt.ylabel("Probability")
plt.xlabel("Number of Sources Binaries per realization")
plt.tight_layout()

#plt.savefig("plots_sigma_76/step_2/76_no_sources_mm13.pdf")



In [ ]:
# File contents are the following:
# RA_tot, DEC_tot, gw_freq_vec, strain_vec, mchirp_rec,q_rec, gal_cat_name, dist_list, mstar_list, 
# save_p, gal_choice, T_z_list, mergRate_list, t2c_list, z_list, r_inf_list, friction_list, 
# hardening_list, num_zeros

In [12]:
#complies all the detected skies - skies where there is potential detectable source

no_of_skies = len(RA)
dest_file = "../../detectedSkies/new_format_detectedSkies.txt"    



for jj in range(no_of_skies):
        filename = str(jj)
   
        for ii in range(len(RA[jj])):
            look_up_freq = find_nearest(freq_choice, freq[jj][ii]) # what is the closest GW freq (out of 87)?
            healpix_map = hp.read_map('../../healpix_maps/strain_map_freq_'+str(look_up_freq)+'Hz.fits')
            pixNo = hp.pixelfunc.ang2pix(nside, pi/2-DEC[jj][ii], pi+RA[jj][ii]) # ± angles for correct display in healpix
            pixStrain = healpix_map[pixNo]
            if strain[jj][ii] > pixStrain and strain[jj][ii]>1e-15:  
                with open(dest_file, 'a+') as f:
                    f.write('{0} {1} {2} {3} {4} {5} {6} {7} {8} {9} {10} {11} {12} {13} {14}\n'.format(RA[jj][ii], 
                    DEC[jj][ii], look_up_freq, strain[jj][ii], filename, mchirp_rec[jj][ii],q_rec[jj][ii], dist_list[jj][ii], mstar_list[jj][ii], 
                    save_p[jj][ii], gal_choice[jj][ii], T_z_list[jj][ii], mergeRate_list[jj][ii], t2c_list[jj][ii], z_list[jj][ii]))


NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file


NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file


NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file


NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file


NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file


...

NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file


NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file


NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file


NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file
INDXSCHM = IMPLICIT
NSIDE = 64
ORDERING = RING in fits file


IndexError: list index out of range